Задача - определить диалект португальского языка по фразе.

Данные взяты из субтитров кофнеренции TED

### Подготовка данных

In [2]:
!wget https://object.pouta.csc.fi/OPUS-TED2020/v1/mono/pt.txt.gz
!wget https://object.pouta.csc.fi/OPUS-TED2020/v1/mono/pt_br.txt.gz
!gunzip pt.txt.gz
!gunzip pt_br.txt.gz


--2023-04-15 10:19:27--  https://object.pouta.csc.fi/OPUS-TED2020/v1/mono/pt.txt.gz
Resolving object.pouta.csc.fi (object.pouta.csc.fi)... 86.50.254.19
Connecting to object.pouta.csc.fi (object.pouta.csc.fi)|86.50.254.19|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11610902 (11M) [application/gzip]
Saving to: ‘pt.txt.gz’

pt.txt.gz           100%[===================>]  11.07M  4.32MB/s    in 2.6s    

2023-04-15 10:19:31 (4.32 MB/s) - ‘pt.txt.gz’ saved [11610902/11610902]

--2023-04-15 10:19:31--  https://object.pouta.csc.fi/OPUS-TED2020/v1/mono/pt_br.txt.gz
Resolving object.pouta.csc.fi (object.pouta.csc.fi)... 86.50.254.19
Connecting to object.pouta.csc.fi (object.pouta.csc.fi)|86.50.254.19|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 14802314 (14M) [application/gzip]
Saving to: ‘pt_br.txt.gz’

pt_br.txt.gz        100%[===================>]  14.12M  4.94MB/s    in 2.9s    

2023-04-15 10:19:35 (4.94 MB/s) - ‘pt_br.txt.gz’ save

In [35]:
import pandas as pd

pt = pd.read_csv('pt.txt', sep='\t', names=['text'])
pt['target'] = 'pt'
pt_br = pd.read_csv('pt_br.txt', sep='\t', names=['text'])
pt_br['target'] = 'pt_br'
data = pd.concat([pt[:10000], pt_br[:10000]], ignore_index=True)

In [4]:
data

text target
0      Em meados do século XVI, os italianos eram cat...     pt
1                   Porém, este dom tinha um alto preço.     pt
2      Para impedir a alteração da voz, esses cantore...     pt
3      Conhecidos por "castrati", estas vozes agudas ...     pt
4      Embora o crescimento vocal retardado possa pro...     pt
...                                                  ...    ...
49995  Como você acha que seria o mundo se você fosse...  pt_br
49996                            Bem, a resposta é nada.  pt_br
49997  A razão por que você não consegue enxergar no ...  pt_br
49998  Para ver uma maçã, a luz tem que atingir a maç...  pt_br
49999  Então, as retinas em seus olhos recebem o refl...  pt_br

[50000 rows x 2 columns]

### Файнтюн модели

In [5]:
!pip install transformers
import transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 98.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 102.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 12.0 MB/s eta 0:00:00


In [6]:
!pip install datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 14.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 28.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 51.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 13.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 kB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 kB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 7.3 MB/s eta 0:00:00


In [46]:
from sklearn.model_selection import train_test_split
from transformers import AutoModelForSequenceClassification, AutoTokenizer, TrainingArguments, Trainer, IntervalStrategy
from datasets import load_metric, Dataset, ClassLabel


X_train, X_test, y_train, y_test = train_test_split(
    data,
    data['target'],
    test_size=0.1,
    random_state=42
)

tokenizer = AutoTokenizer.from_pretrained('adalbertojunior/distilbert-portuguese-cased', do_lower_case=False)

class_label = ClassLabel(names=['pt','pt_br'])

def tokenize(text):
    tokens = tokenizer(text['text'], padding=True, truncation=True, max_length=256, add_special_tokens = True)
    tokens['label'] = class_label.str2int(text['target'])
    return tokens

train_ds = Dataset.from_pandas(X_train).map(tokenize, batched=True)
test_ds = Dataset.from_pandas(X_test).map(tokenize, batched=True)

train_ds.set_format('torch', columns=['input_ids', 'attention_mask', 'label'])
test_ds.set_format('torch', columns=['input_ids', 'attention_mask', 'label'])

Map:   0%|          | 0/18000 [00:00<?, ? examples/s]

Map:   0%|          | 0/2000 [00:00<?, ? examples/s]

In [12]:
from transformers import BertForSequenceClassification, AdamW, BertConfig

model = BertForSequenceClassification.from_pretrained(
   'adalbertojunior/distilbert-portuguese-cased',
    num_labels = 2,
    output_attentions = False, 
    output_hidden_states = False,
)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at adalbertojunior/distilbert-portuguese-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [14]:
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'
model.to(device)
device

'cuda'

In [33]:
params = list(model.named_parameters())

print('The BERT model has {:} different named parameters.\n'.format(len(params)))

print('==== Embedding Layer ====\n')

for p in params[0:5]:
    print("{:<55} {:>12} {}".format(p[0], str(tuple(p[1].size())), p[1].requires_grad))

print('\n==== First Transformer ====\n')

for p in params[5:21]:
    print("{:<55} {:>12} {}".format(p[0], str(tuple(p[1].size())), p[1].requires_grad))

print('\n==== Output Layer ====\n')

for p in params[-4:]:
    print("{:<55} {:>12} {}".format(p[0], str(tuple(p[1].size())), p[1].requires_grad))

The BERT model has 105 different named parameters.

==== Embedding Layer ====

bert.embeddings.word_embeddings.weight                  (29794, 768) False
bert.embeddings.position_embeddings.weight                (512, 768) False
bert.embeddings.token_type_embeddings.weight                (2, 768) False
bert.embeddings.LayerNorm.weight                              (768,) False
bert.embeddings.LayerNorm.bias                                (768,) False

==== First Transformer ====

bert.encoder.layer.0.attention.self.query.weight          (768, 768) False
bert.encoder.layer.0.attention.self.query.bias                (768,) False
bert.encoder.layer.0.attention.self.key.weight            (768, 768) False
bert.encoder.layer.0.attention.self.key.bias                  (768,) False
bert.encoder.layer.0.attention.self.value.weight          (768, 768) False
bert.encoder.layer.0.attention.self.value.bias                (768,) False
bert.encoder.layer.0.attention.output.dense.weight        (768, 76

In [16]:
for parameter in model.parameters():
    parameter.requires_grad = False
for parameter in model.classifier.parameters():
    parameter.requires_grad = True

In [47]:
import numpy as np

training_args = TrainingArguments(
    output_dir="./trainer_out",
    learning_rate=2e-4,
    per_device_train_batch_size=256,
    per_device_eval_batch_size=256,
    num_train_epochs=5,
    weight_decay=0.01,
    evaluation_strategy=IntervalStrategy.EPOCH,
)

metric = load_metric('accuracy')

def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)

# # transfer learning
# for module in list(model.modules())[:-3]:
#     for param in module.parameters():
#         param.requires_grad = False

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_ds,
    eval_dataset=test_ds,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=355, training_loss=0.6338723196110255, metrics={'train_runtime': 724.7707, 'train_samples_per_second': 124.177, 'train_steps_per_second': 0.49, 'total_flos': 5961032939520000.0, 'train_loss': 0.6338723196110255, 'epoch': 5.0})

In [53]:
trainer.train()

TrainOutput(global_step=355, training_loss=0.6281896456866197, metrics={'train_runtime': 723.41, 'train_samples_per_second': 124.411, 'train_steps_per_second': 0.491, 'total_flos': 5961032939520000.0, 'train_loss': 0.6281896456866197, 'epoch': 5.0})

In [54]:
trainer.save_model('./pt_br_model')

In [55]:
!tar jcpvf model.tar.bz2 pt_br_model

pt_br_model/
pt_br_model/tokenizer_config.json
pt_br_model/training_args.bin
pt_br_model/vocab.txt
pt_br_model/pytorch_model.bin
pt_br_model/tokenizer.json
pt_br_model/config.json
pt_br_model/special_tokens_map.json


In [42]:
!ls -al ./pt_br_model/*

-rw-r--r-- 1 root root       752 Apr 15 10:51 ./pt_br_model/config.json
-rw-r--r-- 1 root root 265629621 Apr 15 10:51 ./pt_br_model/pytorch_model.bin
-rw-r--r-- 1 root root       125 Apr 15 10:51 ./pt_br_model/special_tokens_map.json
-rw-r--r-- 1 root root       395 Apr 15 10:51 ./pt_br_model/tokenizer_config.json
-rw-r--r-- 1 root root    678043 Apr 15 10:51 ./pt_br_model/tokenizer.json
-rw-r--r-- 1 root root      3579 Apr 15 10:51 ./pt_br_model/training_args.bin
-rw-r--r-- 1 root root    209528 Apr 15 10:51 ./pt_br_model/vocab.txt


In [44]:
!ls -al

total 317924
drwxr-xr-x 1 root root      4096 Apr 15 10:51 .
drwxr-xr-x 1 root root      4096 Apr 15 10:18 ..
drwxr-xr-x 4 root root      4096 Apr 13 13:29 .config
-rw-r--r-- 1 root root 252222673 Apr 15 10:52 model.tar.bz2
drwxr-xr-x 2 root root      4096 Apr 15 10:51 pt_br_model
-rw-r--r-- 1 root root  41144160 Dec  3  2020 pt_br.txt
-rw-r--r-- 1 root root  32155453 Dec  3  2020 pt.txt
drwxr-xr-x 1 root root      4096 Apr 13 13:30 sample_data
drwxr-xr-x 3 root root      4096 Apr 15 10:25 trainer_out


In [56]:
!cp model.tar.bz2 /content/drive/MyDrive

In [58]:
print(transformers.__version__)

4.28.1
